In [ ]:
# ..... look at lizard heart data ..... #

In [2]:
library(Seurat)

In [3]:
# list of stages and samples
# path0 = '/data/suresh/heart/lizard/stage'
path0 = 'data/'
stages = rep(c('9', '13', '16'), each = 3)
samples = rep(c('1', '2', '3'), 3)

mt_genes = c('nad1', 'nad2', 'cox1', 'cox2', 'atp8', 'atp6', 'cox3',
             'nad3', 'nad4l', 'nad4', 'nad5', 'nad6', 'cob')
length(mt_genes)

[1] 13

In [4]:
# load data
id = 7
mat = Read10X_h5(paste0(path0, 'stage', stages[id], '_sample', samples[id], 
                        '/outs/filtered_feature_bc_matrix.h5'))

# rename MT genes with prefix
genes = rownames(mat)
ids = match(mt_genes, genes)
ids <- ids[!is.na(ids)]
genes[ids] <- paste0('MT-', genes[ids])
rownames(mat) <- genes

In [5]:
# change column names
currstage = paste0('stage', stages[id])
currsmp = paste0('sample', samples[id])
smp = paste0(currstage, '_', currsmp, '_')
colnames(mat) <- paste0(smp, colnames(mat))

sce = CreateSeuratObject(counts = mat)
sce

Warning message:
“Feature names cannot have underscores ('_'), replacing with dashes ('-')”


An object of class Seurat 
22732 features across 10290 samples within 1 assay 
Active assay: RNA (22732 features, 0 variable features)
 1 layer present: counts

In [6]:
# Compute percent mito ratio
sce$mitoRatio <- PercentageFeatureSet(object = sce, pattern = "^MT-")
sce$mitoRatio <- sce@meta.data$mitoRatio / 100

# Add number of genes per UMI for each cell to metadata
sce$log10GenesPerUMI <- log10(sce$nFeature_RNA) / log10(sce$nCount_RNA)
sce$stage = currstage
sce$sample = currsmp
sce@meta.data[1:2,]

orig.ident nCount_RNA nFeature_RNA
stage16_sample1_AAACCCACAGCTGTCG-1 stage16    1309        715        
stage16_sample1_AAACCCACATGTGACT-1 stage16    4854       2105        
                                   mitoRatio    log10GenesPerUMI stage  
stage16_sample1_AAACCCACAGCTGTCG-1 0.0137509549 0.9157399        stage16
stage16_sample1_AAACCCACATGTGACT-1 0.0004120313 0.9015633        stage16
                                   sample 
stage16_sample1_AAACCCACAGCTGTCG-1 sample1
stage16_sample1_AAACCCACATGTGACT-1 sample1

In [7]:
# save 10x filtered counts matrix w/o removing doublets, bad cells, etc.
saveRDS(sce, file = paste0(smp, 'raw_data.rds'))